In [1]:
import tensorflow as tf
from sklearn.datasets import make_classification
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import classification_report, confusion_matrix

2025-11-12 17:18:24.255077: I external/local_xla/xla/tsl/cuda/cudart_stub.cc:31] Could not find cuda drivers on your machine, GPU will not be used.
2025-11-12 17:18:24.312342: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2025-11-12 17:18:25.689783: I external/local_xla/xla/tsl/cuda/cudart_stub.cc:31] Could not find cuda drivers on your machine, GPU will not be used.


# Synthetic Data Generation

In [2]:
# synthetic data generation of 2000 samples
X, y = make_classification(n_samples=2000,
                            n_features=20, 
                            n_classes=2, 
                            n_informative=15, 
                            n_redundant=5, 
                            random_state=42)
scaler = StandardScaler()
X = scaler.fit_transform(X)

# Train/Validation/Test Splits

In [3]:
# Split into train (64%), val (16%), test (20%)
X_trainval, X_test, y_trainval, y_test = train_test_split(X, y, test_size=0.2, random_state=42)
X_train, X_val, y_train, y_val = train_test_split(X_trainval, y_trainval, test_size=0.2, random_state=42)

# Model Setup

In [11]:
# Feed Forward Neural Network Initalization
model = tf.keras.Sequential([
    tf.keras.layers.Dense(64, activation='relu', input_shape=(20,)),
    tf.keras.layers.Dense(32, activation='relu'),
    tf.keras.layers.Dense(1, activation='sigmoid')
])

## Training Hyperparameters Setup

In [5]:
#optimizer and loss setup
model.compile(
    optimizer=tf.keras.optimizers.Adam(learning_rate=0.05),
    loss='binary_crossentropy',
    metrics=['accuracy']
)

## Learning Rate Scheduler

In [6]:
# Learning rate scheduler
lr_scheduler = tf.keras.callbacks.ReduceLROnPlateau(
    monitor='val_loss',        # metric to monitor
    factor=0.5,                # reduce by a factor
    patience=2,                # wait 2 epochs before reducing LR
    min_lr=1e-5,               # don't reduce below this
    verbose=1
)

## Early Stopping Logic

In [7]:
# 3. Early stopping callback with patience and loss threshold
early_stop = tf.keras.callbacks.EarlyStopping(
    monitor='val_loss',
    patience=3,
    min_delta=0.01,  # minimum change to be considered an improvement
    restore_best_weights=True,
    verbose=1
)

Model Training

In [8]:
# 4. Train the model
model.fit(
    X_train, y_train,
    validation_data=(X_val, y_val),
    epochs=100,
    callbacks=[early_stop, lr_scheduler],  # your custom early stopping + LR scheduler
    verbose=2
)

Epoch 1/100
40/40 - 1s - 29ms/step - accuracy: 0.8359 - loss: 0.3691 - val_accuracy: 0.9187 - val_loss: 0.2269 - learning_rate: 0.0500
Epoch 2/100
40/40 - 0s - 3ms/step - accuracy: 0.9102 - loss: 0.2240 - val_accuracy: 0.9438 - val_loss: 0.1643 - learning_rate: 0.0500
Epoch 3/100
40/40 - 0s - 3ms/step - accuracy: 0.9477 - loss: 0.1400 - val_accuracy: 0.9531 - val_loss: 0.1484 - learning_rate: 0.0500
Epoch 4/100
40/40 - 0s - 3ms/step - accuracy: 0.9547 - loss: 0.1338 - val_accuracy: 0.9344 - val_loss: 0.1857 - learning_rate: 0.0500
Epoch 5/100

Epoch 5: ReduceLROnPlateau reducing learning rate to 0.02500000037252903.
40/40 - 0s - 3ms/step - accuracy: 0.9555 - loss: 0.1402 - val_accuracy: 0.9219 - val_loss: 0.1695 - learning_rate: 0.0500
Epoch 6/100
40/40 - 0s - 3ms/step - accuracy: 0.9688 - loss: 0.0904 - val_accuracy: 0.9656 - val_loss: 0.1186 - learning_rate: 0.0250
Epoch 7/100
40/40 - 0s - 3ms/step - accuracy: 0.9812 - loss: 0.0491 - val_accuracy: 0.9688 - val_loss: 0.1048 - learning

evaluation metrics

In [9]:
# 5. Evaluate on test set
y_pred_probs = model.predict(X_test).flatten()
y_pred = (y_pred_probs >= 0.5).astype(int)


print("\n Test Set Evaluation:")
print(classification_report(y_test, y_pred))
print("Confusion Matrix:")
print(confusion_matrix(y_test, y_pred))

13/13 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step 

 Test Set Evaluation:
              precision    recall  f1-score   support

           0       0.95      0.99      0.97       207
           1       0.99      0.95      0.97       193

    accuracy                           0.97       400
   macro avg       0.97      0.97      0.97       400
weighted avg       0.97      0.97      0.97       400

Confusion Matrix:
[[205   2]
 [ 10 183]]
